In [8]:
import pandas as pd
import numpy as np
from collections import defaultdict, Counter
from pca import pca
import plotly.express as px
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from os import path
from sklearn.manifold import Isomap
import warnings
from sklearn.neighbors import LocalOutlierFactor
warnings.filterwarnings('ignore')

from Prostate_Cancer_TFM.Data_Analysis.EHRtemporalVariability.quality_metrics import estimateMSVmetrics

In [94]:
def split_per_hospital(df, hospi_col):
    # create a determinist order!
    hospital_set = sorted(list(set(hospi_col)))
    output = []
    for hospital in hospital_set:
        output.append(df[hospi_col == hospital])
    return output


def filter_site_outliers(arr):
    lof = LocalOutlierFactor()
    outlier_labels = lof.fit_predict(arr)
    # filter based on the labels
    filtered_arr = arr[outlier_labels == 1]
    return filtered_arr


def preprare_data_DQ_count(sites_df, dim_reduction='PCA',
                        n_bins=10, outlier_filtering=False, n_components=3):
    if dim_reduction == 'PCA':
        dim_reductor = pca(n_components=n_components, normalize=True, verbose=0)
    elif dim_reduction == 'Isomap':
        dim_reductor = Isomap(n_components=3)
    else:
        raise ValueError(f'Unvalid dimensionality reduction technique: {dim_reduction}')

    # Concat and apply PCA // IMPORTANT - the pca library does not have fit as standalone method
    pca_ = dim_reductor.fit_transform(pd.concat(sites_df).drop(columns='dep', axis=1))

    print('PCA explained variance:', pca_.get("variance_ratio"))
    # fig, axis = dim_reductor.plot()
    # fig.show()
    # apply the transformation to the different sites
    site_vector = []
    for df in sites_df:
        low_dim_df_ = np.array(dim_reductor.transform(df.drop(columns='dep', axis=1)))
        # IMPORTANT - outlier filtering PER SITE
        if outlier_filtering:
            low_dim_df_ = filter_site_outliers(low_dim_df_)
        histogram = np.histogramdd(low_dim_df_, bins=n_bins)[0]#.reshape(1, -1)
        flatten_histogram = histogram.reshape(1, -1)
        site_vector.append((flatten_histogram / flatten_histogram.sum())[0])
    return site_vector


def plot_scatter_3d(df, hospital_col_, outlier_filtering=False, width=800, height=800):
    if df.shape[1] < 3:
        print(f"Dimensions of the DF should at least be 3. Current dimension: {df.shape[1]}")
        return
    colnames = df.columns.values

    # PCA to reduce to 3 components for 3D plot
    pca_output = pca(n_components=3, normalize=True, verbose=0).fit_transform(df)
    pca_data = pca_output.get('PC')
    print(pca_output)
    print(f'Explained variance Ratio: {sum(pca_output.get("variance_ratio"))}')
    pca_data['hospital'] = hospital_col_

    if outlier_filtering:
        non_outliers_dfs = []
        dataframes = split_per_hospital(pca_data, pca_data.hospital)
        for df in dataframes:
            actual_hospital = df.hospital.iloc[0]
            df_not_outlier = filter_site_outliers(df.drop('hospital', axis=1))
            df_not_outlier['hospital'] = actual_hospital
            non_outliers_dfs.append(df_not_outlier)
        pca_data = pd.concat(non_outliers_dfs)

    # Create 3D scatter plot
    fig = px.scatter_3d(pca_data, x="PC1", y="PC2", z="PC3", color="hospital",
                        title="PCA 3D data", labels={"PC1": "1st comp", "PC2": "2nd comp", "PC3": "3rd comp"}, 
                        hover_data=["PC1", "PC2", "PC3", "hospital"], width=width, height=height)

    fig.update_layout(
                    title=f"PCA projected data in 3D",
                    title_x=0.5,
                    font=dict(family="Courier New, monospace", size=14),
                    legend=dict(title="Hospital"))

    return fig

# Data Reading and Preprocessing

In [95]:
# Variables  withut high correlation
take_variables = [
    'diagnostics_Image-original_Mean',
    'diagnostics_Image-original_Minimum',
    'diagnostics_Image-original_Maximum',
    'diagnostics_Mask-original_VoxelNum',
    'diagnostics_Mask-original_VolumeNum',
    'diagnostics_Image-interpolated_Mean',
    'diagnostics_Image-interpolated_Minimum',
    'diagnostics_Image-interpolated_Maximum',
    'diagnostics_Mask-interpolated_VoxelNum',
    'diagnostics_Mask-interpolated_Mean',
    'original_shape_Elongation',
    'original_shape_Flatness',
    'original_shape_LeastAxisLength',
    'original_shape_MinorAxisLength',
    'original_shape_Sphericity',
    'original_firstorder_10Percentile',
    'original_firstorder_90Percentile',
    'original_firstorder_Entropy',
    'original_firstorder_InterquartileRange',
    'original_firstorder_Kurtosis',
    'original_firstorder_MeanAbsoluteDeviation',
    'original_firstorder_Median',
    'original_firstorder_RootMeanSquared',
    'original_firstorder_Skewness',
    'original_firstorder_Variance',
    'original_glcm_ClusterProminence',
    'original_glcm_ClusterTendency',
    'original_glcm_Contrast',
    'original_gldm_LargeDependenceLowGrayLevelEmphasis',
    'original_glrlm_GrayLevelNonUniformityNormalized',
    'original_glrlm_HighGrayLevelRunEmphasis',
    'original_glrlm_LongRunLowGrayLevelEmphasis',
    'original_glrlm_RunLengthNonUniformity',
    'original_glrlm_ShortRunEmphasis',
    'original_glszm_GrayLevelNonUniformity',
    'original_glszm_GrayLevelNonUniformityNormalized',
    'original_glszm_HighGrayLevelZoneEmphasis',
    'original_glszm_LargeAreaEmphasis',
    'original_glszm_SizeZoneNonUniformity',
    'original_glszm_SizeZoneNonUniformityNormalized',
    'original_ngtdm_Busyness',
    'dep']

In [96]:
data = pd.read_csv('Prostate_Cancer_TFM/Data_Analysis/EHRtemporalVariability/numeric_features_t2w_train.csv')

data.dropna(subset='dep', inplace=True)
display(data['dep'].value_counts())

data_sucio = data[take_variables]

drop_values = [2, 3, 4]
filtered_df = data_sucio[~data_sucio['dep'].isin(drop_values)]

hospitals = split_per_hospital(filtered_df,filtered_df['dep'])


dep
17.0    5659
5.0     4563
19.0    3714
21.0    3372
20.0    3282
7.0     3160
15.0    2384
16.0    1764
12.0    1260
14.0     938
18.0     772
1.0      498
8.0      443
4.0      261
3.0        3
2.0        3
Name: count, dtype: int64

In [97]:
hospitals[0]

diagnostics_Image-original_Mean  diagnostics_Image-original_Minimum  \
138                         878.485991                                 0.0   
139                         650.053701                                 0.0   
140                         810.846448                                 0.0   
141                         702.069963                                 0.0   
288                         695.570174                                 0.0   
...                                ...                                 ...   
30194                       698.094128                                 0.0   
30195                       469.325350                                 0.0   
30196                       746.550648                                 0.0   
30197                       893.314638                                 0.0   
31616                        92.887129                                 0.0   

       diagnostics_Image-original_Maximum  diagnostics_Mask-original_VoxelNum  \
138                           2519.778076                           3043200.0   
139                          10314.078125                           6451200.0   
140                           5702.976562                          18933600.0   
141                           3924.451172                           4330800.0   
288                           2935.712891                           6537600.0   
...                                   ...                                 ...   
30194                         3010.228516                           5883840.0   
30195                         2186.943604                           4852224.0   
30196                         2721.520996                          13641600.0   
30197                         2776.679932                           2832000.0   
31616                         1006.000000                            986700.0   

       diagnostics_Mask-original_VolumeNum  \
138                                    1.0   
139                                    1.0   
140                                    1.0   
141                                    2.0   
288                                    1.0   
...                                    ...   
30194                                  1.0   
30195                                  1.0   
30196                                  2.0   
30197                                  1.0   
31616                                  1.0   

       diagnostics_Image-interpolated_Mean  \
138                           1.791883e-05   
139                           1.075256e-16   
140                           1.883968e-01   
141                          -4.147897e-03   
288                           4.401651e-02   
...                                    ...   
30194                         5.641142e-02   
30195                        -1.670599e-04   
30196                         3.341506e-01   
30197                         9.889742e-02   
31616                         3.902797e-01   

       diagnostics_Image-interpolated_Minimum  \
138                                 -1.872716   
139                                 -1.287522   
140                                 -2.343296   
141                                 -1.985837   
288                                 -1.339213   
...                                       ...   
30194                               -1.326614   
30195                               -1.692336   
30196                               -1.409262   
30197                               -1.897626   
31616                               -2.222931   

       diagnostics_Image-interpolated_Maximum  \
138                                  3.373075   
139                                 19.140955   
140                                  8.774518   
141                                  7.019631   
288                                  4.313049   
...                                       ...   
30194                                4.393835   
30195     

# Computing PCA and Distance Metrics

In [98]:
hospitals_preprocessed = preprare_data_DQ_count(hospitals,outlier_filtering=False, n_components=3, n_bins=10)

PCA explained variance: [0.2678621  0.14408923 0.11492552]


In [99]:
vectors = np.column_stack(hospitals_preprocessed)
msv_complete_data = estimateMSVmetrics(vectors)

13


In [102]:
msv_complete_data

{'GPD': 0.560683982760375,
 'SPOs': array([0.47305029, 0.57751905, 0.53130548, 0.47755983, 0.41881746,
        0.50198053, 0.28552124, 0.18521005, 0.56455236, 0.500165  ,
        0.33184402, 0.43297639, 0.09991942]),
 'Vertices': array([[-0.40061454, -0.17254661,  0.02022851],
        [ 0.08770231,  0.30279993,  0.42989564],
        [-0.01012632,  0.2987789 , -0.38878777],
        [-0.0164972 ,  0.29061781,  0.33105186],
        [-0.34664392, -0.17104298, -0.0065128 ],
        [-0.15149481,  0.30618744, -0.31306105],
        [ 0.23759966, -0.10508509,  0.04434394],
        [ 0.07180178,  0.02600685, -0.15295927],
        [-0.43540626, -0.26662157,  0.10443112],
        [ 0.34228821, -0.30971235,  0.00868369],
        [ 0.30013001, -0.06105113, -0.00501782],
        [ 0.31362142, -0.22342217, -0.10705446],
        [ 0.00763965,  0.08509096,  0.03475841]]),
 'DistsM': array([[0.        , 0.98679394, 0.92198757, 0.93583586, 0.78377473,
         0.85176277, 0.97412937, 0.94847181, 0.664276

In [113]:
from sklearn.decomposition import PCA

def plot_scatter_3d(df, hospital_col_, outlier_filtering=False, width=800, height=800):
    if df.shape[1] < 3:
        print(f"Dimensions of the DF should at least be 3. Current dimension: {df.shape[1]}")
        return
    colnames = df.columns.values

    # PCA to reduce to 3 components for 3D plot
    pca = PCA(n_components=3)
    pca_output = pca.fit_transform(df)
    print(f'Explained variance: {pca.explained_variance_ratio_}')
    
    pca_data = pd.DataFrame(data=pca_output, columns=['PC1', 'PC2', 'PC3'])
    pca_data['hospital'] = hospital_col_

    if outlier_filtering:
        non_outliers_dfs = []
        dataframes = split_per_hospital(pca_data, pca_data.hospital)
        for df in dataframes:
            actual_hospital = df.hospital.iloc[0]
            df_not_outlier = filter_site_outliers(df.drop('hospital', axis=1))
            df_not_outlier['hospital'] = actual_hospital
            non_outliers_dfs.append(df_not_outlier)
        pca_data = pd.concat(non_outliers_dfs)

    # Create 3D scatter plot
    fig = px.scatter_3d(pca_data, x="PC1", y="PC2", z="PC3", color="hospital",
                        title="PCA 3D data", labels={"PC1": "1st comp", "PC2": "2nd comp", "PC3": "3rd comp"}, 
                        hover_data=["PC1", "PC2", "PC3", "hospital"], width=width, height=height)

    fig.update_layout(title=f"PCA projected data in 3D",
                      title_x=0.5,
                      font=dict(family="Courier New, monospace", size=14),
                      legend=dict(title="Hospital"))

    return fig

In [116]:
from sklearn.decomposition import PCA
pca = PCA(n_components=3,)
pca_output = pca.fit_transform(filtered_df.drop(columns='dep', axis=1))
print(f'Explained variance: {pca.explained_variance_ratio_}')

pca_data = pd.DataFrame(data=pca_output, columns=['PC1', 'PC2', 'PC3'])

Explained variance: [9.99999995e-01 3.76411771e-09 1.45511089e-09]


In [118]:
from pca import pca
pca_output = pca(n_components=3, normalize=True, verbose=0).fit_transform(filtered_df.drop(columns='dep', axis=1))
pca_data = pca_output.get('PC')
print(f'Explained variance Ratio: {sum(pca_output.get("variance_ratio"))}')
print(pca_output.get("variance_ratio"))

Explained variance Ratio: 0.5268768582165536
[0.2678621  0.14408923 0.11492552]


In [84]:
plot_scatter_3d(filtered_df,filtered_df['dep'])

Explained variance: [9.99999995e-01 3.53439593e-09 1.29935014e-09]


In [103]:
def plotMSV2d(msvMetrics: dict, n_by_source: list[int], label_sources: list[str], title: str, height=800, width=800):
    sphere_max_size = 100
    scale_factor = sphere_max_size / max(n_by_source)
    fig = px.scatter(x=msvMetrics['Vertices'][:, 2],#x=msvMetrics['Vertices'][:, 0],
                     y=msvMetrics['Vertices'][:, 1],

                     color=label_sources,
                     size=[n * scale_factor for n in n_by_source],
                     size_max=sphere_max_size,
                     text=label_sources,
                     height=height,
                     width=width,
                     labels={'x': '1st comp',
                             'y': '2nd comp'}
                     )
    fig.update_layout(title=title,
                      title_x=0.5,
                      font=dict(
                          family="Courier New, monospace",
                          size=14,
                      ),
                      legend=dict(
                          title="Hospital"
                      ),
                      template="seaborn"
                      )
    return fig

In [104]:
counter_hospital = Counter(filtered_df['dep'])

In [105]:
hospitals_ordered = sorted(list(set(counter_hospital.keys())))
n_by_hospital = [counter_hospital[h] for h in hospitals_ordered]

In [106]:
msv2d=plotMSV2d(msvMetrics=msv_complete_data, n_by_source=n_by_hospital, title="Multi-Source Variability plot", label_sources=hospitals_ordered, width=1000)

In [107]:
msv2d

In [108]:
def plotMSV(msvMetrics: dict, n_by_source: list[int], label_sources: list[str], title: str, height=800, width=800):
    sphere_max_size = 100
    scale_factor = sphere_max_size / max(n_by_source)
    fig = px.scatter_3d(x=msvMetrics['Vertices'][:, 0],
                        y=msvMetrics['Vertices'][:, 1],
                        z=msvMetrics['Vertices'][:, 2],
                        color=label_sources,
                        size=[n * scale_factor for n in n_by_source],
                        size_max=sphere_max_size,
                        text=label_sources,
                        height=height,
                        width=width
                        )
    fig.update_layout(title=title,
                      title_x=0.5,
                      font=dict(
                          family="Courier New, monospace",
                          size=14,
                      ),
                      legend=dict(
                          title="Pilot"
                      )
                      )
    return fig

In [109]:
msv3d=plotMSV(msvMetrics=msv_complete_data, n_by_source=n_by_hospital, title="Multi-Source Variability plot", label_sources=hospitals_ordered, width=1000)

In [111]:
msv3d

In [75]:
msv3d

In [38]:
import plotly.graph_objects as go
from plotly import data

def dumbell(title: str, height=800, width=800, missing=False):
    colors = ['black','#636EFA', '#EF553B', '#00CC96', '#AB63FA']
    questionnaires = ['Complete','','Socio-demographic', 'Health Literacy', 'Health Data', 'Risk behaviours and healthy lifestyles',
                      'Psychological distress', 'Quality of life', 'Health Care Empowerment',
                      'Interpersonal Communication', 'Use of health care services']

    if missing:
        # gpds = [0.933,None, 0.876, #0, 0, 0.877, 0, 0.593, 0, 0.603, 0.888]
        # 
        # spos = [0.75,	0.771,	0.787,	0.839 ,None,None,None,None,#0.877, 0.601, 0.877, 0.601,0, 0, 0, 0, 0,0,0,0, 0.647, 0.753, 0.879, 0.679,0,0,0,0,0.333,0.333,1,0.333,0,0,0,0,0.35,
        #         0.339, 0.997,0.349,0.652,0.824,0.846,0.673]
        #MODIFICAR ESTE ENTIRE POR EL BUENO
        entire = [0.933,0.75,	0.771,	0.787,	0.839,None,None,None,None,None,0.876,0.877, 0.601, 0.877, 0.601,0, 0, 0, 0,0,0,0,0,0,0,0.877,0.647,0.753, 0.879, 0.679,
                  0,0,0,0,0,0.593,0.333,0.333,1,0.333,0,0,0,0,0,0.603,0.35,0.339, 0.997,0.349,0.888,0.652,0.824,0.846,0.673]
    else:
        # gpds = [0.833,None, 0.882, 0.897, 0.452, 0.789, 0.854, 0.838, #0.905, #0.911,0.914]
        # spos = [0.692,	0.701,	0.706,	0.711,None,None,None,None, 0.791, 0.714, 0.785, 0.727, 0.854, 0.839, 0.663, 0.671, 0.473, 0.291, 0.273, 0.488, #0.691, 0.649, 0.682,
        #         0.638, 0.782, 0.674, 0.724, 0.701, 0.746, 0.662, 0.701, 0.717, 0.778, 0.721, 0.776, 0.778, #0.798, 0.721,
        #         0.836, 0.718, #0.801, 0.732, 0.849, 0.703]
        
        entire = [0.833,0.692,	0.701,	0.706,	0.711,None,None,None,None,None,0.882,0.791, 0.714, 0.785, 0.727,0.897,0.854, 0.839, 0.663, 0.671,0.452,0.473, 0.291, 0.273, 0.488,0.789,0.691, 0.649, 0.682,0.638,0.854,0.782, 0.674, 0.724, 0.701,0.838,0.746, 0.662, 0.701, 0.717,0.905,0.778, 0.721, 0.776, 0.778,0.911,0.798, 0.721, 0.836, 0.718,0.914,0.801, 0.732, 0.849, 0.703]

    
    values_per_questionnaire = [entire[i * 5:(i + 1) * 5] for i in range(len(questionnaires))]
    
    fig = go.Figure()
    
    pilots = ['GPD', 'Austria','Greece', 'Spain', 'United Kingdom']
    opciones = ['circle','cross','diamond','square','triangle-up']
    
    #PARTE DE SPO
    for i in range(5):
        fig.add_trace(go.Scatter(
            x=questionnaires,
            y=[values_per_questionnaire[j][i] if i < len(values_per_questionnaire[j]) else None for j in range(len(questionnaires))],

           
            name=f'SPO {pilots[i]}' if i != 0 else f'GPD',
            #marker_color=colors[i % len(colors)],
            mode="markers",
            marker=dict(
                color=colors[i % len(colors)],
                symbol=opciones[i%len(opciones)],
                size=13
            ),
        ))
    
    
    fig.update_layout(
            height=height,
            width=width,
            title=dict(
                text=title,
                x=0.5,
                xanchor='center',
                yanchor='top',
                font=dict(
                    family="Arial, sans-serif",
                    size=24,
                    color='black'
                )
                
            ),
            legend = dict(
                title="Pilots",
                font=dict(
                    family="Arial, sans-serif",
                    size=14,
                    color='black'
                ),
                bgcolor='rgba(0,0,0,0)',
                bordercolor='black',
                borderwidth=1
            ),
            template="simple_white",
            xaxis=dict(
                tickvals=list(range(len(questionnaires))),
                ticktext=questionnaires,
                title='Questionnaires',
                showgrid=False  # Mantener las líneas verticales ocultas
            ),
            yaxis=dict(
                showgrid=True,  # Mostrar las líneas horizontales
                gridcolor='lightgrey'  # Color de las líneas horizontales
            ),
        )
    return fig